In [1]:
!pip install --quiet huggingface_hub datasets pyarrow

from huggingface_hub import login

login(token="HUGGINGFACE_TOKEN")

/home/zafir/miniconda3/envs/dissertation/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
import os
import requests
import logging
import csv
from requests.adapters import HTTPAdapter, Retry
from datasets import load_dataset_builder, load_dataset
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm.auto import tqdm

In [3]:
logging.basicConfig(level=logging.INFO)

builder = load_dataset_builder("bigcode/the-stack-v2", "TypeScript")
total_ts = builder.info.splits["train"].num_examples
logging.info(f"▶︎ There are {total_ts:,} TS files in train split.")

INFO:root:▶︎ There are 37,284,635 TS files in train split.


In [4]:
ds = load_dataset(
    "bigcode/the-stack-v2",
    "TypeScript",
    split="train",
    streaming=True
)

In [7]:
logging.basicConfig(level=logging.INFO, format='%(message)s')
RESULTS_CSV = "outputs/results.csv"

with open(RESULTS_CSV, "w", newline="", encoding="utf-8") as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["repo", "revision_id", "path", "url", "status", "local_path"])

    count = 0
    for ex in tqdm(ds):
        repo     = ex["repo_name"]
        sha      = ex["revision_id"]
        rel_path = ex["path"].lstrip("/")
        url      = f"https://raw.githubusercontent.com/{repo}/{sha}/{rel_path}"

        if rel_path.lower().endswith((".ts", ".tsx")):
            writer.writerow([repo, sha, rel_path, url, "pending", ""])
            count += 1

print(f"\n✅ Done! Logged {count} TypeScript file URLs to {RESULTS_CSV}.")

16776808it [3:09:28, 1447.47it/s]'(MaxRetryError('HTTPSConnectionPool(host=\'huggingface.co\', port=443): Max retries exceeded with url: /datasets/bigcode/the-stack-v2/resolve/7408bfbcfd48e5833d62fd3dba48afd20d109473/data/TypeScript/train-00002-of-00005.parquet (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x70b1f3560cd0>: Failed to resolve \'huggingface.co\' ([Errno -2] Name or service not known)"))'), '(Request ID: 81dc2f5c-7b99-4eaa-b5f3-c7260dc8e6dd)')' thrown while requesting GET https://huggingface.co/datasets/bigcode/the-stack-v2/resolve/7408bfbcfd48e5833d62fd3dba48afd20d109473/data/TypeScript/train-00002-of-00005.parquet
16776953it [3:09:29, 1266.67it/s]Retrying in 1s [Retry 1/5].
16778178it [3:09:30, 1257.09it/s]'(MaxRetryError('HTTPSConnectionPool(host=\'huggingface.co\', port=443): Max retries exceeded with url: /datasets/bigcode/the-stack-v2/resolve/7408bfbcfd48e5833d62fd3dba48afd20d109473/data/TypeScript/train-00002-of-00005.parquet (Caused 


✅ Done! Logged 37236325 TypeScript file URLs to outputs/results.csv.


In [ ]:
import csv
import os
import subprocess
from concurrent.futures import ThreadPoolExecutor, as_completed

CSV_PATH = "outputs/results.csv"
OUTPUT_DIR = "output/ts-output"
NUM_WORKERS = 8

os.makedirs(OUTPUT_DIR, exist_ok=True)

def download_url(row):
    url = row[3].strip()
    if not url:
        return None

    filename = url.split("/")[-1]
    out_path = os.path.join(OUTPUT_DIR, filename)

    if os.path.exists(out_path):
        print(f"✓ Skipping existing: {filename}")
        return None

    cmd = ["aria2c", "--dir", OUTPUT_DIR, url]
    print(f"→ Downloading: {url}")
    try:
        subprocess.run(cmd, check=True, stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)
        return out_path
    except subprocess.CalledProcessError:
        print(f"✗ Failed: {url}")
        return None

with open(CSV_PATH, newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    next(reader)  # Skip header
    rows = list(reader)

with ThreadPoolExecutor(max_workers=NUM_WORKERS) as executor:
    futures = [executor.submit(download_url, row) for row in rows]

    completed = 0
    for future in as_completed(futures):
        result = future.result()
        if result:
            completed += 1
            print(f"✓ Completed: {result}")

print(f"\n✅ Done! {completed} files downloaded to {OUTPUT_DIR}")

✓ Skipping existing: listenings.service.ts
✓ Skipping existing: error-utils.ts
✓ Skipping existing: contrat-delete-dialog.component.ts
✓ Skipping existing: 07-intervals-timers.ts
✓ Skipping existing: app.component.spec.ts
✓ Skipping existing: log_sum_exp.ts
✓ Skipping existing: bookEventHandler.ts
✓ Skipping existing: video-try.component.spec.ts
✓ Skipping existing: lib.d.ts
✓ Skipping existing: api.ts
✓ Skipping existing: app.component.ts
✓ Skipping existing: player.service.ts
✓ Skipping existing: list.component.ts
✓ Skipping existing: position-square.ts
✓ Skipping existing: user.ts
✓ Skipping existing: injector.ts
✓ Skipping existing: parse-comments.spec.ts
✓ Skipping existing: gestion.tiempo.module.ts
✓ Skipping existing: nav.component.ts
✓ Skipping existing: company-response.model.ts
✓ Skipping existing: homepage.module.ts
✓ Skipping existing: index.d.ts
✓ Skipping existing: textfield-controller.component.ts
✓ Skipping existing: ListLicenseManagerReportGeneratorsCommand.ts
✓ Skippi

#Unused Code Snippets

In [ ]:
logging.basicConfig(level=logging.INFO, format='%(message)s')
OUTPUT_ROOT = "output/ts-output"
FAILED_CSV  = "output/failures.csv"
os.makedirs(OUTPUT_ROOT, exist_ok=True)

session = requests.Session()

def fetch_and_write(ex):
    repo     = ex["repo_name"]
    sha      = ex["revision_id"]
    rel_path = ex["path"].lstrip("/")

    # skip non-TS files
    if not rel_path.lower().endswith((".ts", ".tsx")):
        return {"out_path": None, "meta": None}

    url = f"https://raw.githubusercontent.com/{repo}/{sha}/{rel_path}"
    try:
        res = session.get(url, timeout=(5, 10))
        res.raise_for_status()
        code = res.text
    except Exception as e:
        return {
            "out_path": None,
            "meta": {"repo": repo, "sha": sha, "rel_path": rel_path, "url": url}
        }

    # Write fetched file
    safe_repo = repo.replace("/", "_")
    flat_name = f"{safe_repo}_{rel_path.replace('/', '_')}"
    out_path  = os.path.join(OUTPUT_ROOT, flat_name)
    with open(out_path, "w", encoding="utf-8") as f:
        f.write(code)

    return {"out_path": out_path, "meta": None}

written = 0
with open(FAILED_CSV, "w", newline="", encoding="utf-8") as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["repo", "revision_id", "path", "url"])

    futures = []
    with ThreadPoolExecutor(max_workers=8) as exe:
        for ex in ds:
            futures.append(exe.submit(fetch_and_write, ex))

        for future in tqdm(as_completed(futures), total=len(futures)):
            result = future.result()
            if result["out_path"]:
                written += 1
                logging.info(f"→ {written}: {result['out_path']}")
            elif result["meta"]:
                m = result["meta"]
                writer.writerow([m["repo"], m["sha"], m["rel_path"], m["url"]])

print(f"\n✅ Done! Wrote {written} files. Failed fetches logged to {FAILED_CSV}")


Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
Connection pool is full, discarding connection: raw.githubusercontent.com. Connection pool size: 10
